# Utilisation d'un modèle word2vec entrainé sur des milliards de données (wikipedia + web)

In [97]:
import tensorflow as tf
import numpy as np 
import tensorflow.compat.v1 as tf

#si vous avez un tf 2.x
tf.disable_v2_behavior() 

import math
import pandas as pd
import re
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from ast import literal_eval

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
from gensim.models import KeyedVectors 
data_path = "/content/drive/MyDrive/FilRougeNLP/"
# for download : https://drive.google.com/file/d/0B7XkCwpI5KDYNlNUTTlSS21pQmM/edit?usp=sharing
filename = 'GoogleNews-vectors-negative300.bin'
fileLocation = data_path+filename
fileLocation
model = KeyedVectors.load_word2vec_format(fileLocation, binary=True)

In [115]:
def test(row):
   return np.zeros(300)

In [122]:
#converters='{"Body_A": literal_eval, "Body_Q": literal_eval}'
df = pd.read_csv(data_path+'preprocessed_data.csv', converters={"Body_A": literal_eval, "Body_Q": literal_eval})
df = df[:25000]
df = df[["Body_Q", "Body_A"]]
df["A"] = df.apply(test, axis=1)
df["Q"] = df.apply(test, axis=1)
df_test = df[12500:]
df_train = df[:12500]

In [123]:
df_train

Body_Q  ...                                                  Q
0  [p, using, photoshop, javascript, api, find, f...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1  [p, using, photoshop, javascript, api, find, f...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2  [p, using, photoshop, javascript, api, find, f...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3  [p, using, photoshop, javascript, api, find, f...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4  [p, cross, platform, python, application, need...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
5  [p, cross, platform, python, application, need...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
6  [p, cross, platform, python, application, need...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
7  [p, starting, work, hobby, project, python, co...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
8  [p, starting, work, hobby, project, python, co...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
9  [p, starting, work, hobby, project, python, co...  ...  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

[10 rows x 4 columns]

In [124]:
for index, row in df_train.iterrows():

    for word in df_train.loc[index]['Body_A']:
      if word in model.vocab:
        print(model[word])
        df_train.loc[index]['A'] = np.add(df_train.loc[index]['A'], model[word]) 
      #  df_train.loc[index]['A'] = np.concatenate((df_train.loc[index]['A'], model[word]))
    for word in df_train.loc[index]['Body_Q']:
      if word in model.vocab:
       df_train.loc[index]['Q'] = np.add(df_train.loc[index]['Q'], model[word]) 
    df_train.loc[index]['A'] = np.divide(df_train.loc[index]['A'], np.full(300, index+1))
    df_train.loc[index]['Q'] = np.divide(df_train.loc[index]['Q'], np.full(300, index+1))
    print(df_train.loc[index]['A'])
    # print(df_train.loc[index]['Q'])

Streaming output truncated to the last 5000 lines.
[ 4.82487632e-03 -5.99148832e-02  4.96890256e-03  4.06153761e-02
  2.14598980e-02  5.41538373e-02  2.79410742e-02  1.35384593e-02
  2.46284734e-02 -4.63764220e-02 -5.76104643e-03 -7.02847689e-02
 -7.71980211e-02  6.97086602e-02  3.05335466e-02  2.29001585e-02
  1.02546625e-01  1.04851045e-01 -3.19738090e-02 -9.16006342e-02
 -3.54664424e-03 -2.01636627e-02 -1.57708637e-02  4.55122665e-02
 -1.26743019e-01 -8.35351720e-02 -2.53486037e-02  1.23862498e-01
  1.21702105e-02 -6.53878748e-02 -6.48117736e-02  8.38952418e-03
 -1.33080170e-01 -5.44418879e-02 -5.47299422e-02  5.01211025e-02
 -8.41112807e-02  5.35777323e-02  3.52864079e-02 -5.00490889e-03
 -1.25590816e-01 -7.77741298e-02  1.41865769e-02  3.71587500e-02
  5.18494193e-03 -3.39901745e-02  4.32078466e-02 -3.94631661e-02
 -3.80229056e-02 -3.79868993e-03 -4.75286320e-02  1.59004882e-01
  5.58821484e-02  2.49165259e-02  3.37021202e-02 -6.53878748e-02
 -5.87626733e-02 -5.50179929e-02 -2.232

In [ ]:
for index, row in df_test.iterrows():

    for word in df_test.loc[index]['Body_A']:
      if word in model.vocab:
        print(model[word])
        df_test.loc[index]['A'] = np.add(df_test.loc[index]['A'], model[word]) 
      #  df_train.loc[index]['A'] = np.concatenate((df_train.loc[index]['A'], model[word]))
    for word in df_test.loc[index]['Body_Q']:
      if word in model.vocab:
       df_test.loc[index]['Q'] = np.add(df_test.loc[index]['Q'], model[word]) 
    df_test.loc[index]['A'] = np.divide(df_test.loc[index]['A'], np.full(300, index+1))
    df_test.loc[index]['Q'] = np.divide(df_test.loc[index]['Q'], np.full(300, index+1))
    print(df_test.loc[index]['A'])
    # print(df_train.loc[index]['Q'])

Streaming output truncated to the last 5000 lines.
[ 0.07310092  0.03268949 -0.1075922   0.04144101 -0.05199431 -0.03101641
  0.01750304  0.0218788  -0.07773407  0.07567489 -0.01222639 -0.14311306
 -0.0212353  -0.02535366 -0.06203282 -0.07670448  0.04401499  0.02084921
 -0.06898256 -0.00855847 -0.02290839 -0.05611267  0.05096472  0.08030805
  0.01261248 -0.00868717 -0.10244424  0.0648642   0.15237938 -0.08236723
 -0.010682    0.08854477 -0.00669234 -0.04324279 -0.02406667  0.03294689
 -0.01788913  0.06074583 -0.00242919  0.09987026 -0.01132549 -0.00701408
  0.02406667  0.08700038 -0.00727148 -0.06640857  0.03835224  0.01698824
  0.03655046 -0.01879002  0.010682    0.0013996   0.14826101 -0.07361571
  0.0638346  -0.05173691  0.08442641 -0.04324279  0.06846776  0.03552087
  0.06846776 -0.01698824 -0.02535366 -0.01750304 -0.07001214  0.01190464
 -0.01763174 -0.06640857 -0.04787595 -0.00711061  0.03886703 -0.02998682
 -0.02728414 -0.05611267 -0.042728    0.11891769  0.0957519  -0.12097687


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
[ 8.72450024e-02  4.08439972e-02 -1.37535911e-02  7.50195906e-02
 -3.83433439e-02 -6.14049211e-02  4.55674529e-02 -6.47391230e-02
  4.89016585e-02  4.50117514e-02  7.22410828e-02 -9.50248092e-02
  2.06998494e-02 -6.47391230e-02 -1.05027422e-01  1.63931698e-02
  9.28020105e-02  4.33446504e-02  1.14474334e-01 -5.00130579e-02
  8.72450024e-02  1.17252834e-01  5.86264171e-02 -4.50117514e-02
  1.43092917e-02 -1.20864892e-02 -3.91768962e-02 -4.44560498e-03
  2.48676036e-02  5.41808121e-02 -3.11192367e-02  2.59790048e-02
  3.75097953e-02 -3.59468861e-03  4.58453037e-02  1.01693220e-01
  9.94704142e-02 -9.55805108e-02  2.70904060e-02 -8.89120996e-03
  1.11140134e-02 -1.16349827e-03 -1.34062776e-02 -2.83407327e-02
 -2.70904060e-02  3.91768962e-02 -1.11834751e-02  4.58453037e-02
 -6.55726790e-02  4.27889489e-02  9.65529867e-03  9.05792043e-02
  1.68794077e-02 -8.55778977e-02  3.83433439e-02 -2.77850330e-02
 -7.27967843e-02 -4.27889489e-02  5.306

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
[-1.68790277e-02  3.69318910e-02 -3.00071612e-02  1.12526856e-01
 -6.26110956e-02 -4.64533940e-02 -2.69775912e-02  4.58763316e-02
 -2.26496365e-02 -2.13512499e-02 -3.28924656e-02 -9.11756083e-02
 -2.68333275e-02  4.41451520e-02 -6.08799122e-02  2.71218568e-02
  4.40008845e-03  1.46573439e-01 -1.52199781e-02 -4.93386984e-02
 -1.07910365e-01 -6.08799122e-02  3.17383446e-02 -1.57970395e-02
 -4.55878042e-02 -3.77974808e-02 -1.30415738e-01  1.11949794e-01
 -5.65519594e-02 -2.15496146e-03  3.39023210e-02 -5.36666550e-02
 -1.21182770e-01 -9.00214836e-02 -1.30415738e-01  2.68693920e-03
 -5.13584092e-02  9.46379676e-02 -5.45322448e-02  4.47222106e-02
  4.87616360e-02 -7.32867196e-02 -9.29067880e-02  3.27482000e-02
  4.27024998e-02  1.99085977e-02 -4.50107418e-02 -5.39551824e-02
 -1.00264316e-02  8.83624330e-03 -8.13655704e-02  8.94444212e-02
 -7.73261487e-02  3.80860120e-02  4.81845774e-02  6.34766892e-02
 -3.08727529e-02 -2.87087746e-02  1.096

...

Streaming output truncated to the last 5000 lines.
  0.03126547 -0.01458473 -0.01021804 -0.00807837  0.09362174 -0.07056564
 -0.05868825 -0.05205089 -0.00991238 -0.02174609  0.00694303  0.04471486
 -0.00925737  0.07196298  0.01061105 -0.05135222 -0.07440832  0.02192076
 -0.03301214  0.01711741  0.07336032  0.06707229 -0.01196472  0.07510699
  0.00585136  0.03685483 -0.01109138 -0.08908039  0.0375535   0.0155454
 -0.04419086  0.00399552  0.01248872 -0.09082706  0.02218276 -0.0069867
 -0.00026746 -0.05624291 -0.01078571  0.03283748 -0.03458415 -0.04244418
  0.02602545 -0.04034818 -0.09012839 -0.1313499  -0.08349103  0.05589357
 -0.02620011  0.02183343  0.00262001 -0.02445344 -0.02777212 -0.077203
 -0.06427761 -0.06777096 -0.05659224  0.0391255  -0.02654945 -0.0530989
 -0.09082706 -0.00999971 -0.09292307  0.00960671 -0.04925621  0.00458502
  0.00641903 -0.03895083 -0.07231231 -0.00873337 -0.04890688 -0.02672412
  0.02637478 -0.05903759  0.02759745  0.00615703  0.06253093  0.02532678
 -0.0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
  5.94274364e-02 -2.95531023e-02  2.39315890e-02 -4.91480939e-02
 -2.24860571e-02  1.11787826e-01 -6.45671040e-02  4.97905537e-02
  6.78597065e-03  1.93741475e-03  3.01955622e-02 -1.50335357e-01
 -3.69413793e-02 -9.07472987e-03  6.10335805e-02  1.45356292e-02
  6.52095675e-02 -3.66201475e-02  8.48045573e-02  3.59776914e-02
 -2.48952769e-02  5.26816174e-02 -1.05363235e-01  5.30028492e-02
 -3.98324430e-02  1.32507123e-02  2.37709749e-02  4.81844060e-02
  5.13967015e-02 -1.22870235e-02 -1.56759933e-01 -7.83799663e-02
 -3.53352316e-02  2.23254412e-02  5.46089932e-02 -5.07542416e-02
  4.33659665e-02  3.95112149e-02 -8.43227096e-03  5.49302250e-02
  7.45252147e-02 -3.42109278e-02 -1.18212409e-01  1.91131476e-02
  6.10335805e-02 -6.13548122e-02 -5.49302250e-02 -1.02150939e-01
  4.30447385e-02 -1.40537852e-02 -2.24860571e-02  7.42039904e-02
 -2.24860571e-02  5.58136031e-03  1.02793397e-02 -7.35615268e-02
 -8.28771815e-02  1.96752995e-02  2.184

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
[-2.12307256e-02 -6.78347573e-02  9.45026241e-03  1.23630147e-02
  4.63451222e-02  3.44352014e-02  8.85476619e-02  3.65064926e-02
  8.34988896e-03 -1.04211792e-02  8.23337957e-02 -4.58272994e-02
 -3.46941128e-02 -5.98732382e-03  2.12307256e-02  2.57616732e-02
  3.78010496e-02  2.22663712e-02  3.54384840e-03  4.56331158e-03
  5.59895672e-03 -3.08104437e-02 -6.99060485e-02  6.78347573e-02
 -1.77095324e-01  4.71218564e-02  2.47583934e-03  5.54070175e-02
  1.98067147e-02 -5.67015745e-02 -5.12644351e-02  1.98067147e-02
 -9.89041179e-02 -9.57971811e-02  1.22335590e-02 -3.83188725e-02
  4.11668979e-02 -3.22344564e-02  4.60862108e-02 -8.73825606e-03
 -1.25571983e-02 -9.26902443e-02 -6.93882257e-02  5.51481061e-02
  2.67973188e-02 -6.93882257e-02 -2.73151416e-02  1.43048493e-02
 -1.72176007e-02 -8.05861410e-03 -4.78985906e-02  6.49867356e-02
  8.12981501e-02  5.92906885e-02  6.14914345e-04 -1.90299805e-02
 -9.16545987e-02 -9.83862951e-02 -7.767

In [ ]:
df_test.to_csv('word2vec_train.zip', index=False,
          compression=compression_opts)
df_train.to_csv('word2vec_test.zip', index=False,
          compression=compression_opts)